In [ ]:
!pip install transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 63.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 30.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 118.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 84.4 MB/s eta 0:00:00


In [ ]:
!pip install decord einops timm==0.4.12 tensorboardX

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.6/13.6 MB 69.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 377.0/377.0 kB 42.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 14.4 MB/s eta 0:00:00


In [ ]:
import os
import sys
import json
import warnings
import math
import argparse
import logging
import random
import gc
import tqdm

from collections import OrderedDict

import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.backends.cudnn as cudnn
import torch.utils.checkpoint as cp
from torch.utils.data import Dataset
from torch.utils.data._utils.collate import default_collate
from timm.models import create_model
from timm.models.layers import trunc_normal_
from timm.models.registry import register_model
from timm.loss import SoftTargetCrossEntropy
from timm.utils import accuracy
from functools import partial

In [ ]:
%cd /content
!git clone https://github.com/OpenGVLab/VideoMAEv2

/content
Cloning into 'VideoMAEv2'...
remote: Enumerating objects: 128, done.
remote: Counting objects: 100% (12/12), done.
remote: Compressing objects: 100% (9/9), done.
remote: Total 128 (delta 3), reused 3 (delta 3), pack-reused 116
Receiving objects: 100% (128/128), 995.38 KiB | 1.54 MiB/s, done.
Resolving deltas: 100% (57/57), done.


In [ ]:
%cd /content/VideoMAEv2
from utils import (
    load_state_dict,
)
from models.modeling_finetune import PatchEmbed, Block
from optim_factory import (
    LayerDecayValueAssigner,
    get_parameter_groups,
)
%cd /content/

/content/VideoMAEv2
/content


In [ ]:
class_to_label = {}

with open("/content/ucfTrainTestlist/classInd.txt", 'r') as f:
    for line in f:
        label, class_name = line.split()
        class_to_label[class_name] = label

modes = ['train', 'test']

for mode in modes:
    files = [
        f"/content/ucfTrainTestlist/{mode}list01.txt",
        f"/content/ucfTrainTestlist/{mode}list02.txt",
        f"/content/ucfTrainTestlist/{mode}list03.txt",
    ]

    output_file_path = f"/content/UCF101/{'val' if mode == 'test' else mode}.csv"

    with open(output_file_path, 'w') as outfile:
        for file_path in files:
            with open(file_path, 'r') as infile:
                for line in infile:
                    line_text = line.strip()
                    if mode == 'train':
                        video_path, label = line_text.split(' ')
                    else:
                        video_path = line_text
                        class_name = os.path.dirname(line_text)
                        label = class_to_label[class_name]
                    outfile.write(f"/content/UCF101/{video_path} {label}\n")

In [ ]:
import torch
import numpy as np
import cv2
from PIL import Image
from torchvision.transforms import Compose, Resize, CenterCrop, ToTensor, Normalize

class RawVideoExtractorCV2:
    def __init__(self, size=224, frame_sampling_rate=4, clip_len=16, num_crops=3, num_segments=6):
        self.size = size
        self.frame_sampling_rate = frame_sampling_rate
        self.clip_len = clip_len
        self.num_crops = num_crops
        self.num_segments = num_segments
        self.transform = self._setup_transforms(self.size)

    def _setup_transforms(self, n_px):
        return Compose([
            Resize((self.size, self.size)),
            ToTensor(),
            Normalize((0.48145466, 0.4578275, 0.40821073), (0.26862954, 0.26130258, 0.27577711)),
        ])

    def _spatial_crop(self, img_pil):
        if self.num_crops == 1:
            return [CenterCrop(self.size)(img_pil)]

        w, h = img_pil.size
        short_side = min(w, h)

        if w < h:
            intervals = np.linspace(0, h - short_side, self.num_crops)
            crops = [img_pil.crop((0, int(interval), short_side, int(interval) + short_side)) for interval in intervals]
        else:
            intervals = np.linspace(0, w - short_side, self.num_crops)
            crops = [img_pil.crop((int(interval), 0, int(interval) + short_side, short_side)) for interval in intervals]

        return crops

    def video_to_tensor(self, video_file):
        cap = cv2.VideoCapture(video_file)

        total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))

        if self.num_segments == 1:
            start_frame = (total_frames - self.clip_len) // 2
            end_frame = start_frame + self.clip_len * self.frame_sampling_rate
            frames_to_extract = list(range(start_frame, end_frame, self.frame_sampling_rate))
        else:
            frames_per_segment = total_frames // self.num_segments
            frames_to_extract = range(0, total_frames, self.frame_sampling_rate)

        final_frames = []

        for idx in frames_to_extract:
            cap.set(cv2.CAP_PROP_POS_FRAMES, idx)
            ret, frame = cap.read()
            if not ret:
                break
            frame_pil = Image.fromarray(cv2.cvtColor(frame, cv2.COLOR_BGR2RGB))
            cropped_frames = self._spatial_crop(frame_pil)
            cropped_transformed_frames = [self.transform(crop) for crop in cropped_frames]
            final_frames.append(torch.stack(cropped_transformed_frames))

        while len(final_frames) < self.clip_len:
            final_frames.append(final_frames[-1])

        final_frames = [torch.stack([frame[i] for frame in final_frames]) for i in range(self.num_crops)]
        final_tensor = torch.stack(final_frames)

        return final_tensor

In [ ]:
class VideoClsTestDataset(Dataset):
    """Load your own video classification dataset."""

    def __init__(self, anno_path,
                 videoExtractor,
                 data_root='',
                 num_segment=3,
                 num_crop=3,
                 crop_size=224):
        self.anno_path = anno_path
        self.data_root = data_root
        self.num_segment = num_segment
        self.videoExtractor = videoExtractor

        cleaned = pd.read_csv(self.anno_path, header=None, delimiter=' ')
        self.dataset_samples = list(
            cleaned[0].apply(lambda row: os.path.join(self.data_root, row)))
        self.label_array = list(cleaned.values[:, 1])


    def __getitem__(self, index):
        buffer, sample, new_index = self.load_and_check_video(index)
        return buffer, self.label_array[new_index], sample.split("/")[-1].split(".")[0]

    def load_and_check_video(self, index):
        sample = self.dataset_samples[index]
        buffer = self.videoExtractor.video_to_tensor(sample)
        while len(buffer) == 0:
            warnings.warn("Video {} not correctly loaded.".format(sample))
            index = np.random.randint(self.__len__())
            sample = self.dataset_samples[index]
            buffer = self.load_video(sample)
        return buffer, sample, index

    def __len__(self):
        return len(self.dataset_samples)

In [ ]:
LOG_10000 = math.log(10000.0)

def get_sinusoid_encoding_table(n_position, d_hid):
    ''' Sinusoid position encoding table '''

    position = torch.arange(n_position, dtype=torch.float).unsqueeze(1)
    div_term = torch.exp(torch.arange(0, d_hid, 2, dtype=torch.float) *
                         -(LOG_10000 / d_hid))

    position = position * div_term

    sinusoid_table = torch.zeros(n_position, d_hid)
    sinusoid_table[:, 0::2] = torch.sin(position)  # dim 2i
    if d_hid > 1:
        sinusoid_table[:, 1::2] = torch.cos(position)  # dim 2i+1

    return sinusoid_table.unsqueeze(0)

In [ ]:
class VisionTransformer(nn.Module):
    """ Vision Transformer with support for patch or hybrid CNN input stage
    """

    def __init__(self,
                img_size=224,
                patch_size=16,
                in_chans=3,
                embed_dim=768,
                depth=12,
                num_heads=12,
                mlp_ratio=4.,
                qkv_bias=False,
                qk_scale=None,
                drop_rate=0.,
                attn_drop_rate=0.,
                drop_path_rate=0.,
                norm_layer=nn.LayerNorm,
                init_values=0.,
                use_learnable_pos_emb=False,
                init_scale=0.,
                all_frames=16,
                tubelet_size=2,
                with_cp=False,
                cos_attn=False,
                clip_embed_dim=768):
        super().__init__()

        self.initialize_params(
            embed_dim, tubelet_size, img_size, patch_size, in_chans, all_frames,
            use_learnable_pos_emb, drop_rate, norm_layer,
            with_cp, init_scale, clip_embed_dim)

        self.build_model(depth, num_heads, mlp_ratio, qkv_bias, qk_scale, drop_rate,
                         attn_drop_rate, drop_path_rate, init_values, cos_attn)

        self.initialize_weights()

    def initialize_params(self, embed_dim, tubelet_size, img_size, patch_size,
                          in_chans, all_frames, use_learnable_pos_emb, drop_rate,
                          norm_layer, with_cp, init_scale, clip_embed_dim):
        self.embed_dim = embed_dim
        self.num_features = embed_dim
        self.tubelet_size = tubelet_size
        self.patch_embed = PatchEmbed(
            img_size=img_size, patch_size=patch_size, in_chans=in_chans,
            embed_dim=embed_dim, num_frames=all_frames, tubelet_size=tubelet_size)
        self.with_cp = with_cp
        self.norm_layer = norm_layer
        self.init_pos_embed(use_learnable_pos_emb, self.patch_embed.num_patches, embed_dim)
        self.pos_drop = nn.Dropout(p=drop_rate)
        self.final_norm = self.norm_layer(embed_dim)
        self.head = nn.Linear(self.embed_dim, clip_embed_dim)
        self.head.weight.data.mul_(init_scale)
        self.head.bias.data.mul_(init_scale)



    def init_pos_embed(self, use_learnable_pos_emb, num_patches, embed_dim):
        if use_learnable_pos_emb:
            self.pos_embed = nn.Parameter(torch.zeros(1, num_patches, embed_dim))
            trunc_normal_(self.pos_embed, std=.02)
        else:
            self.pos_embed = get_sinusoid_encoding_table(num_patches, embed_dim)


    def build_model(self, depth, num_heads, mlp_ratio, qkv_bias, qk_scale,
                    drop_rate, attn_drop_rate, drop_path_rate, init_values, cos_attn):
        dpr = [x.item() for x in torch.linspace(0, drop_path_rate, depth)]
        self.blocks = nn.ModuleList([
            Block(
                dim=self.embed_dim, num_heads=num_heads, mlp_ratio=mlp_ratio,
                qkv_bias=qkv_bias, qk_scale=qk_scale, drop=drop_rate,
                attn_drop=attn_drop_rate, drop_path=dpr[i],
                norm_layer=self.norm_layer, init_values=init_values,
                cos_attn=cos_attn
            ) for i in range(depth)
        ])
        self.additional_block = Block(
            dim=self.embed_dim, num_heads=num_heads, mlp_ratio=mlp_ratio,
            qkv_bias=qkv_bias, qk_scale=qk_scale, drop=drop_rate,
            attn_drop=attn_drop_rate, drop_path=drop_path_rate,
            norm_layer=self.norm_layer, init_values=init_values,
            cos_attn=cos_attn
        )

    def initialize_weights(self):
        self.apply(self._init_weights)

    def _init_weights(self, m):
        if isinstance(m, nn.Linear):
            trunc_normal_(m.weight, std=.02)
            if m.bias is not None:
                nn.init.constant_(m.bias, 0)
        elif isinstance(m, nn.LayerNorm):
            nn.init.constant_(m.bias, 0)
            nn.init.constant_(m.weight, 1.0)

    def forward(self, x):
        x = self.forward_features(x)
        x = self.head(x)
        return x

    def forward_features(self, x):
        B = x.shape[0]
        x = self.patch_embed(x)
        x = x + self.pos_embed.expand(B, -1, -1).to(x.device).clone().detach()
        x = self.pos_drop(x)
        for blk in self.blocks:
            x = cp.checkpoint(blk, x) if self.with_cp else blk(x)
        x = cp.checkpoint(self.additional_block, x) if self.with_cp else self.additional_block(x)
        return self.final_norm(x.mean(1))


    def get_num_layers(self):
        return len(self.blocks)

    @torch.jit.ignore
    def no_weight_decay(self):
        return {'pos_embed', 'cls_token'}


@register_model
def vit_giant_patch14_224(pretrained=False, **kwargs):
    return VisionTransformer(
        patch_size=14,
        embed_dim=1408,
        depth=40,
        num_heads=16,
        mlp_ratio=48 / 11,
        qkv_bias=True,
        norm_layer=partial(nn.LayerNorm, eps=1e-6),
        **kwargs)

In [ ]:
import argparse

args = argparse.Namespace()
args.model = 'vit_giant_patch14_224'
args.data_set = 'UCF101'
args.nb_classes = 101
args.data_path = '/content/UCF101/'
args.finetune = '/content/vit_g_hybrid_pt_1200e.pth'
args.log_dir = '/content/vit_g_hybrid_pt_1200e_ucf101_ft'
args.output_dir = '/content/'
args.batch_size = 6
args.input_size = 224
args.save_ckpt_freq = 10
args.num_frames = 16
args.sampling_rate = 4
args.num_segment = 1
args.num_crop = 1

args.tubelet_size = 2
args.init_scale = 0.001
args.data_root = ''

args.pin_mem = True

args.drop = 0.0
args.attn_drop_rate = 0.0
args.drop_path = 0.35
args.with_checkpoint = True
args.num_sample = 2

In [ ]:
videoExtractor = RawVideoExtractorCV2(
    size=args.input_size,
    frame_sampling_rate=args.sampling_rate,
    clip_len=args.num_frames,
    num_crops=args.num_crop,
    num_segments=args.num_segment)

test_dataset = VideoClsTestDataset(
    anno_path=os.path.join(args.data_path, 'val.csv'),
    data_root=args.data_root,
    videoExtractor=videoExtractor,
    num_segment=3,
    num_crop=args.num_crop,
    crop_size=args.input_size)

data_loader_test = torch.utils.data.DataLoader(
    test_dataset,
    batch_size=args.batch_size,
    pin_memory=args.pin_mem,
    drop_last=False)

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
if not os.path.exists("model_epoch_1.pth"):
  !cp /content/drive/MyDrive/MSE/model_epoch_0_20230809_174809.pth  /content/model_epoch_1.pth

In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

torch.manual_seed(0)
np.random.seed(0)
random.seed(0)
cudnn.benchmark = True

In [ ]:
model = create_model(
    args.model,
    img_size=args.input_size,
    pretrained=False,
    all_frames=args.num_frames,
    tubelet_size=args.tubelet_size,
    drop_rate=args.drop,
    drop_path_rate=args.drop_path,
    attn_drop_rate=args.attn_drop_rate,
    drop_block_rate=None,
    init_scale=args.init_scale,
    with_cp=args.with_checkpoint,
)

In [ ]:
checkpoint = torch.load('/content/model_epoch_1.pth', map_location='cpu')
checkpoint_model = checkpoint['model_state_dict']

In [ ]:
new_dict = OrderedDict()
for key, value in checkpoint_model.items():
    if key.startswith('module.'):
        new_key = key[7:]
    new_dict[new_key] = value

checkpoint_model = new_dict

In [ ]:
model.load_state_dict(checkpoint_model)
model.eval()
model.to(device)

VisionTransformer(
  (patch_embed): PatchEmbed(
    (proj): Conv3d(3, 1408, kernel_size=(2, 14, 14), stride=(2, 14, 14))
  )
  (pos_drop): Dropout(p=0.0, inplace=False)
  (final_norm): LayerNorm((1408,), eps=1e-06, elementwise_affine=True)
  (head): Linear(in_features=1408, out_features=768, bias=True)
  (blocks): ModuleList(
    (0): Block(
      (norm1): LayerNorm((1408,), eps=1e-06, elementwise_affine=True)
      (attn): Attention(
        (qkv): Linear(in_features=1408, out_features=4224, bias=False)
        (attn_drop): Dropout(p=0.0, inplace=False)
        (proj): Linear(in_features=1408, out_features=1408, bias=True)
        (proj_drop): Dropout(p=0.0, inplace=False)
      )
      (drop_path): Identity()
      (norm2): LayerNorm((1408,), eps=1e-06, elementwise_affine=True)
      (mlp): Mlp(
        (fc1): Linear(in_features=1408, out_features=6144, bias=True)
        (act): GELU(approximate='none')
        (fc2): Linear(in_features=6144, out_features=1408, bias=True)
        (dr

In [ ]:
labels_embedding_path = os.path.join(args.data_path, 'labels-CLIP-embedding.txt')

label_to_embedding = []
with open(labels_embedding_path, 'r') as file:
    label_index = 1
    for line in file:
        label, description, raw_embedding = line.split(' | ')
        embedding = json.loads(raw_embedding)
        label_to_embedding.append(torch.FloatTensor(embedding))

label_to_embedding_tensor = torch.stack(label_to_embedding).to(device)
labels_norm = F.normalize(label_to_embedding_tensor, p=2, dim=1).t()

anno_path = os.path.join(args.data_path, 'val.csv')
label_array = list(pd.read_csv(anno_path, header=None, delimiter=' ').values[:, 1])

In [ ]:
from transformers import CLIPProcessor, CLIPModel

clip_model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
clip_model = clip_model.to(device)

`text_config_dict` is provided which will be used to initialize `CLIPTextConfig`. The value `text_config["id2label"]` will be overriden.
`text_config_dict` is provided which will be used to initialize `CLIPTextConfig`. The value `text_config["bos_token_id"]` will be overriden.
`text_config_dict` is provided which will be used to initialize `CLIPTextConfig`. The value `text_config["eos_token_id"]` will be overriden.


In [ ]:
def calc_embedding(samples, video_mae_embedding_factor=0.75):
  batch_size = samples.shape[0]
  avg_outputs = torch.zeros([batch_size, 768]).to(device)
  if video_mae_embedding_factor == 0:
    for seg in range(args.num_segment):
        video_batchs_segment = samples[:, seg, :, :, :, :]
        for frame_index in range(args.num_frames):
          center_frame = video_batchs_segment[:, :, frame_index, :, :]
          clip_features = clip_model.get_image_features(pixel_values=center_frame).float()
          avg_outputs += clip_features
    avg_outputs /= args.num_frames
  else:
    for seg in range(args.num_segment):
      video_batchs_segment = samples[:, seg, :, :, :, :]
      center_frame = video_batchs_segment[:, :, args.num_frames // 2, :, :]
      clip_features = clip_model.get_image_features(pixel_values=center_frame).float()
      avg_outputs += clip_features * (1 - video_mae_embedding_factor)

    with torch.cuda.amp.autocast(dtype=torch.float16):
      for seg in range(args.num_segment):
          video_batchs_segment = samples[:, seg, :, :, :, :]
          segment_output = model(video_batchs_segment).view(batch_size, -1)
          avg_outputs += segment_output * video_mae_embedding_factor

  avg_outputs /= args.num_segment
  return avg_outputs


In [ ]:
import numpy as np
import torch
import random
from tqdm import tqdm

def compute_accuracy(top_k_indices, targets):
    acc1 = float((top_k_indices[:, 0] == targets).sum()) / len(targets)
    acc5 = float((top_k_indices[:, :5] == targets.unsqueeze(1)).sum(1).sum()) / len(targets)
    return acc1, acc5

all_class_indices = list(range(101))  # Assuming UCF101 has 101 classes.
num_trials = 10
acc1_list = []
acc5_list = []

for trial in tqdm(range(num_trials), desc="Trials"):
    # Randomly select half of the classes
    selected_classes = random.sample(all_class_indices, len(all_class_indices) // 2)

    results = []
    total_targets = []
    total_top5_indices = []

    with torch.no_grad():
        for step, (samples, targets, ids) in enumerate(tqdm(data_loader_test, desc=f"Trial {trial + 1}", leave=False)):
            # Filter out samples that do not belong to the selected classes
            mask = torch.isin(targets, torch.tensor(selected_classes))

            # Convert the mask to indices
            indices = torch.nonzero(mask).squeeze().tolist()

            # Filter using these indices
            samples = samples[indices]
            targets = targets[indices]
            ids = [ids[i] for i in indices]

            if len(samples) == 0:
                continue

            samples = samples.permute(0, 1, 3, 2, 4, 5).to(device, non_blocking=True)
            out_embedding = calc_embedding(samples)
            diffs = (out_embedding.unsqueeze(1) - label_to_embedding_tensor.unsqueeze(0)).pow(2).sum(2)
            _, sorted_indices = torch.sort(diffs, dim=1)

            targets = targets.to(device, non_blocking=True) - 1
            total_targets.extend(targets.tolist())
            total_top5_indices.append(sorted_indices)

    # Compute accuracies
    total_targets = torch.tensor(total_targets).to(device)
    total_top5_indices = torch.cat(total_top5_indices, dim=0)
    acc1, acc5 = compute_accuracy(total_top5_indices, total_targets)
    acc1_list.append(acc1)
    acc5_list.append(acc5)

    print(f"Trial {trial + 1} - Acc1: {acc1:.4f}, Acc5: {acc5:.4f}")

# Report final results
mean_acc1 = np.mean(acc1_list)
std_acc1 = np.std(acc1_list)
mean_acc5 = np.mean(acc5_list)
std_acc5 = np.std(acc5_list)

print(f"Mean Acc1: {mean_acc1:.4f} ± {std_acc1:.4f}, Mean Acc5: {mean_acc5:.4f} ± {std_acc5:.4f}")


In [ ]:
# csv_file = "/content/ucf101_results.csv"
# with open(csv_file, 'w', newline='') as csvfile:
#     fieldnames = ["Video_ID", "True_Label", "Top5_Predicted_Labels"]
#     writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

#     writer.writeheader()
#     for row in results:
#         writer.writerow(row)